<div><center><img src = https://ibm.box.com/shared/static/1judcmjeqh9gchx9d9dogrzhed299rdi.jpeg width=1000></div>

# <center> Weather Data
## <center>with [Polong Lin](www.linkedin.com/in/polonglin) and [Leons Petrazickis](www.linkedin.com/in/leonsp)

## How to use notebooks:
<div><img src=https://ibm.box.com/shared/static/4g2hs88inr5mwx2midhg9j66emuwit9y.gif width=600 align=left></div>

### Try running some code below:

In [1]:
1 + 1 # Shift+Enter to run

2

### Try to insert a cell below, above the line

<hr>

#### Hermes Weather API Key

In [2]:
my_apikey = 'f43934a981fc48f5926e5929d3ee0760' #designated the Cognitive Builder Faire

### Importing modules

In [3]:
import json
import csv
import pandas as pd
import datetime
from datetime import timedelta, date
import time
import requests
import shutil
import os
from geopy.geocoders import Nominatim #converts addr to lat & lon

<br>

#### Address --> Latitude/Longitude - Hacked for Hermes

In [14]:
list_of_parks = {'Confluence Park':'Confluence Park, Denver', 'Commons Park':'Commons Park, Denver','Skyline Park':'Skyline Park, Denver','Washington Park':'Washington Park, Denver'}

park_name = []
latitudes_list = []
longitudes_list = []

for address in list_of_parks:
    geolocator = Nominatim()
    location = geolocator.geocode(list_of_parks[address])
    latitude, longitude = location.latitude, location.longitude
    latitudes_list = latitudes_list + [latitude]
    longitudes_list = longitudes_list + [longitude]
    park_name = park_name + [address]
    print latitude, longitude

print(len(park_name), len(latitudes_list), len(longitudes_list))    
parksDF = pd.DataFrame({'ParkName': park_name, 'latitude':latitudes_list,'longitude': longitudes_list})
parksDF.head()

39.7537572 -105.00848512
39.7571772 -105.005241419
39.7010814 -104.97103449
39.7494626 -104.994226697
(4, 4, 4)


ParkName   latitude   longitude
0  Confluence Park  39.753757 -105.008485
1     Commons Park  39.757177 -105.005241
2  Washington Park  39.701081 -104.971034
3     Skyline Park  39.749463 -104.994227

<br>

# <center> Getting historical weather data

For historical weather, we send API GET requests to:

> `http://api.weather.com/v1/geocode/`**MY_LATITUDE**`/`**MY_LONGITUDE**`/observations/historical.json?apiKey=`**MY_APIKEY**`&units=`**m**`&startDate=`**YYYYMMDD**`&endDate=`**YYYYMMDD**`



Notice in the link that there are parameters that need to be set:
1. **MY_LATITUDE & MY_LONGITUDE:** The latitude and longitude of the weather station. We have prepared a list of weather stations, as described in the next section
1. **MY_APIKEY:** The API key provided to you for api.weather.com
1. **units=m:** You can change m, which is currently set to Metric units:  
    - For en-US or en, the default units of measure code  is English/Imperial. The units code is “e” .
    - For en-gb, the default units of measure is Hybrid-UK. The units code is  “h”.
    - For everything else, the default units of measure is  Metric. The units code is “m”.
1. **startDate and endDate:** The range that you want to retrieve data for. The maximum range between the two dates is 31 days.

**Don't understand the values returned?** Check the API documentation here: [http://goo.gl/DplOKj](http://goo.gl/DplOKj)

#### Set the values for your GET request URL

In [22]:
from itertools import izip

def get_call(lat,lon,start="20170510",end="20170609"):

    units = "m"
    startDate = start
    endDate = end

    url = "http://api.weather.com/v1/geocode/" + str(lat) + "/" + str(lon)+ \
        "/observations/historical.json?apiKey=" + my_apikey + \
        "&units=" + units + "&language=en-US" + \
        "&startDate="+str(startDate) + \
        "&endDate="+str(endDate)

    return url


calls = []
for spot in zip(parksDF['latitude'],parksDF['longitude']):
    calls.append(get_call(spot[0],spot[1]))
    
print calls

['http://api.weather.com/v1/geocode/39.7537572/-105.00848512/observations/historical.json?apiKey=f43934a981fc48f5926e5929d3ee0760&units=m&language=en-US&startDate=20170510&endDate=20170609', 'http://api.weather.com/v1/geocode/39.7571772/-105.005241419/observations/historical.json?apiKey=f43934a981fc48f5926e5929d3ee0760&units=m&language=en-US&startDate=20170510&endDate=20170609', 'http://api.weather.com/v1/geocode/39.7010814/-104.97103449/observations/historical.json?apiKey=f43934a981fc48f5926e5929d3ee0760&units=m&language=en-US&startDate=20170510&endDate=20170609', 'http://api.weather.com/v1/geocode/39.7494626/-104.994226697/observations/historical.json?apiKey=f43934a981fc48f5926e5929d3ee0760&units=m&language=en-US&startDate=20170510&endDate=20170609']


#### GET request for historical data

In [24]:
import requests
data = []
for call in calls:
    print(data)
    data.append(requests.get(call).json())
    



[]
[{u'observations': [{u'primary_wave_period': None, u'primary_swell_direction': None, u'terse_phrase': None, u'expire_time_gmt': 1494406680, u'vis': 16, u'clds': u'BKN', u'wx_icon': 26, u'primary_swell_period': None, u'min_temp': 10, u'primary_wave_height': None, u'uv_index': 0, u'primary_swell_height': None, u'precip_hrly': 0.0, u'uv_desc': u'Low', u'obs_id': u'KBKF', u'water_temp': None, u'pressure_desc': None, u'heat_index': 12, u'wspd': 13, u'rh': 86, u'qualifier_svrty': None, u'valid_time_gmt': 1494399480, u'wc': 12, u'qualifier': None, u'blunt_phrase': None, u'wdir': 240, u'obs_name': u'Aurora/Buckley Afb', u'icon_extd': 2600, u'dewPt': 9, u'pressure': 822.51, u'wdir_cardinal': u'WSW', u'secondary_swell_height': None, u'key': u'KBKF', u'class': u'observation', u'secondary_swell_period': None, u'pressure_tend': None, u'temp': 12, u'gust': None, u'precip_total': None, u'snow_hrly': None, u'day_ind': u'N', u'secondary_swell_direction': None, u'feels_like': 12, u'wx_phrase': u'Clou

In [25]:
first_location_data = data[0]

print(first_location_data.keys())
print(len(first_location_data['observations']))
print('----------------------------------------')
#Count everyobservation in the raw data for test in a minute
count = 0
for location in data:
    count += len(location['observations'])

print count

[u'observations', u'metadata']
828
----------------------------------------
3312


#### JSON to Pandas DataFrame

In [8]:
timestamp = []
measurement = []
value = []


def DataFramify(raw_data):
    final_df = pd.DataFrame()
    for location in raw_data:
        r = location
        for obs in range(1, len(r['observations'])):
            obstime = time.ctime(r['observations'][obs]['valid_time_gmt'])
            timestamp.extend([obstime] * len(r['observations'][0].keys()))
            measurement.extend(r['observations'][obs].keys())
            value.extend(r['observations'][obs].values())

        latitude = [r['metadata']['latitude']] * len(timestamp)
        longitude = [r['metadata']['longitude']] * len(timestamp)
        obs_name = [r['observations'][0]['obs_name']] * len(timestamp)
        
        #todo add column for match ratings and fake some match rating data

        final_df = final_df.append(pd.DataFrame(zip(obs_name, latitude, longitude, timestamp, measurement, value), 
                     columns= ['obs_name', 'latitude', 'longitude', 'timestamp_gmt', 'measurement', 'value']))
    return final_df

full_example_df = DataFramify(data)

full_example_df.head()

full_example_df.tail()
#todo - data makes SINGLE data frame

obs_name  latitude  longitude             timestamp_gmt  \
24835  Aurora/Buckley Afb     39.74    -104.99  Fri Jun  9 23:58:00 2017   
24836  Aurora/Buckley Afb     39.74    -104.99  Fri Jun  9 23:58:00 2017   
24837  Aurora/Buckley Afb     39.74    -104.99  Fri Jun  9 23:58:00 2017   
24838  Aurora/Buckley Afb     39.74    -104.99  Fri Jun  9 23:58:00 2017   
24839  Aurora/Buckley Afb     39.74    -104.99  Fri Jun  9 23:58:00 2017   

                     measurement         value  
24835                    day_ind             N  
24836  secondary_swell_direction          None  
24837                 feels_like            22  
24838                  wx_phrase  Fair / Windy  
24839                   max_temp          None

#### Single variable

In [9]:
precip_total = example_from_second_location[example_from_second_location.measurement == "precip_total"]
precip_total.head()

NameError: name 'example_from_second_location' is not defined

#### Note: API requests are limited to 30-day intervals
Note the API request for historical day have a limitation of requesting 30-day intervals of data at a time.

Use this function to conveniently set 30-day intervals based on your start and end dates:

In [ ]:
def getDates(start_date, end_date, delta = 30):
    '''
    Returns a list of date intervals of delta number of days, that encompasses the entire duration between start_date and end_date
    start_date: starting date in format YYYYMMDD
    end_date: end date in format YYYYMMDD
    delta: set as number of days for the interval; the interval between start_date and end_date; default = 30
    '''
    from datetime import timedelta, date
    delta = delta -1
    #Convert dates to date format
    s = datetime.date(int(str(start_date)[:4]),int(str(start_date)[4:6]),int(str(start_date)[6:]))
    e = datetime.date(int(str(end_date)[:4]),int(str(end_date)[4:6]),int(str(end_date)[6:]))

    #Set delta
    if (int(delta) > 30 or int(delta) < 1):
        raise ValueError('Error: delta out of range. 1 <= delta <= 30')
    else:
        delta = timedelta(days=int(delta))

    days= []
    day_from = s
    while (day_from) < e:
        day_to = day_from + delta
        days.append((day_from.strftime("%Y%m%d"), day_to.strftime("%Y%m%d")))
        #print '...for range %s to %s ...' % (day_from.strftime("%Y%m%d"), day_to.strftime("%Y%m%d"))
        day_from += delta + timedelta(days=int(1))
    return days

In [ ]:
getDates(20170101,20171231,30)

In [26]:
import requests
import datetime

def get_weather_historical(latitude, longitude, startdate, enddate, measurement = "", units = "m"):
    ## Input: 
    ##   latitude
    ##   longitude
    ##   startdate (e.g., "20170608")
    ##   enddate (e.g., "20170609")
    ##   measurement (e.g., "temp") - leave blank ("") to retrieve all weather measurements
    ## Returns: 
    ##    a dataframe
    
    latitude_input = latitude
    longitude_input = longitude
    measurement_input = measurement
    
    possible_measurement = [None, u'', u'blunt_phrase',u'class', u'clds', u'day_ind', u'dewPt', u'expire_time_gmt', 
                            u'feels_like', u'gust', u'heat_index', u'icon_extd', u'key', u'max_temp', u'min_temp',
                            u'obs_id', u'obs_name', u'precip_hrly', u'precip_total', u'pressure', u'pressure_desc', 
                            u'pressure_tend', u'primary_swell_direction', u'primary_swell_height', u'primary_swell_period', 
                            u'primary_wave_height', u'primary_wave_period', u'qualifier', u'qualifier_svrty', u'rh',
                            u'secondary_swell_direction', u'secondary_swell_height', u'secondary_swell_period', u'snow_hrly',
                            u'temp', u'terse_phrase', u'uv_desc', u'uv_index', u'valid_time_gmt', u'vis', u'water_temp', u'wc', 
                            u'wdir', u'wdir_cardinal', u'wspd', u'wx_icon', u'wx_phrase']
    
    if measurement_input not in possible_measurement:
        print("ERROR: Measurement not valid. Please choose from:")
        print(possible_measurement[2:])
        return(None)
    
    timestamp = []
    measurement = []
    value = []
    df = pd.DataFrame()
    
    daterangelist = getDates(startdate,enddate,30)
    
    for daterange in daterangelist:
        url = "http://api.weather.com/v1/geocode/" + str(latitude_input) + "/" + str(longitude_input)+ \
            "/observations/historical.json?apiKey=" + my_apikey + \
            "&units=" + units + "&language=en-US" + \
            "&startDate="+str(daterange[0]) + \
            "&endDate="+str(daterange[1])
        
        r = requests.get(url).json()

        try: 
            if(r['errors']):
                return("[ERROR RETURNED FROM API REQUEST]: " + r['errors'][0]['error']['message'])
        except:
            pass
        
        for obs in range(1, len(r['observations'])):
            obstime = time.ctime(r['observations'][obs]['valid_time_gmt'])
            timestamp.extend([obstime] * len(r['observations'][0].keys()))
            measurement.extend(r['observations'][obs].keys())
            value.extend(r['observations'][obs].values())

        latitude = [r['metadata']['latitude']] * len(timestamp)
        longitude = [r['metadata']['longitude']] * len(timestamp)
        obs_name = [r['observations'][0]['obs_name']] * len(timestamp)

        newdf = pd.DataFrame(zip(obs_name, latitude, longitude, timestamp, measurement, value), 
                     columns= ['obs_name', 'latitude', 'longitude', 'timestamp_gmt', 'measurement', 'value'])
        
        df = df.append(newdf, ignore_index = True)
    
    
    #Fix date formatting
    df['timestamp_gmt'] = pd.to_datetime(df['timestamp_gmt'])
    df['date_gmt'] = df['timestamp_gmt'].apply(lambda x: x.strftime('%Y-%m-%d'))
    
    if measurement_input not in [u'', 'None']:
        #print(measurement)
        df = df[df.measurement == measurement_input]
        
    return(df.reset_index(drop=True))

#### All types of measurements:

In [37]:
final_df = pd.DataFrame()
for spot in zip(parksDF['latitude'],parksDF['longitude']):
    final_df = final_df.append(get_weather_historical(latitude=spot[0],
                           longitude=spot[1],
                            startdate = "20170607",
                             enddate = "20170608",
                             measurement=""))
final_df.head(55)


obs_name  latitude  longitude       timestamp_gmt  \
0   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
1   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
2   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
3   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
4   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
5   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
6   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
7   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
8   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
9   Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
10  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
11  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
12  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
13  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
14  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
15  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
16  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
17  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
18  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
19  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
20  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
21  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
22  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
23  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
24  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
25  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
26  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
27  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
28  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
29  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
30  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
31  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
32  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
33  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
34  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
35  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
36  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
37  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
38  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
39  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
40  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
41  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
42  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
43  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
44  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 01:58:00   
45  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   
46  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   
47  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   
48  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   
49  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   
50  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   
51  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   
52  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   
53  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   
54  Aurora/Buckley Afb     39.75     -105.0 2017-06-07 02:58:00   

                  measurement               value    date_gmt  
0         primary_wave_period                None  2017-06-07  
1     primary_swell_direction                None  2017-06-07  
2                terse_phrase                None  2017-06-07  
3    

#### Specific Measurements Only:

In [ ]:
df_uvindex = get_weather_historical(latitude = 39.83,
                             longitude = -104.65, 
                             startdate = "20170607",
                             enddate = "20170608",
                             measurement="uv_index") # uv_index only
df_uvindex.head()

#### Invalid Measurement Specified

In [ ]:
dontknow = get_weather_historical(latitude = 39.83,
                             longitude = -104.65, 
                             startdate = "20170607",
                             enddate = "20170608",
                             measurement="dontknow")
print(dontknow)

# <center> Want to brush up your skills in data science?
### <center> Check out the free courses available on [IBM Cognitive Class](https://cognitiveclass.ai/courses?utm_source=cbfdenver&utm_medium=notebook):

<div>
<a href = https://cognitiveclass.ai/courses?utm_source=cbfdenver&utm_medium=notebook><img src = https://ibm.box.com/shared/static/66h8iy2qwaai57ldjqj70jgkm9gq9ny3.pn></a></div>